In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from neuralprophet import set_log_level

from tot.datasets.dataset import Dataset
from tot.models.models_darts import RandomForestModel, LinearRegressionModel
from tot.models.models_neuralprophet import NeuralProphetModel
from tot.data_processing import Scaler
from tot.benchmark import SimpleBenchmark
from tot.plotting import plot_plotly

/Users/pediatria/Desktop/TUMai/tot/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
set_log_level("ERROR")

In [3]:
data_location = "https://raw.githubusercontent.com/ourownstory/neuralprophet-data/main/datasets/"
df_ercot = pd.read_csv(data_location + "multivariate/load_ercot_regions.csv")

In [4]:
regions = list(df_ercot)[1:]

In [5]:
df_global = pd.DataFrame()
for col in regions:
    aux = df_ercot[["ds", col]].copy(deep=True)
    aux = aux.copy(deep=True)
    aux = aux.iloc[:26301, :].copy(deep=True)
    aux = aux.rename(columns={col: "y"})
    aux["ID"] = col
    df_global = pd.concat((df_global, aux))

In [6]:
def plot(df, regions=regions):
    fig = go.Figure()

    for region in regions:
        fig.add_trace(
            go.Scatter(
                name=region,
                x=df[df['ID'] == region]['ds'],
                y=df[df['ID'] == region]['y']))
    fig.show()

In [7]:
def filter_ID(df, values):
    return df[df.ID.isin(values)]

In [8]:
chosen_regions = ["WEST", "FAR_WEST", "NORTH_C"]

In [9]:
similar_season_diff_amplitude_2_1 = filter_ID(df_global,chosen_regions)

In [10]:
s = Scaler(StandardScaler(), "per_time_series")
similar_season_diff_amplitude_2_1_scaled, _ = s.transform(similar_season_diff_amplitude_2_1, similar_season_diff_amplitude_2_1)

In [11]:
plot(similar_season_diff_amplitude_2_1_scaled)

In [12]:
dataset_list = [
    Dataset(df=similar_season_diff_amplitude_2_1, name="similar_season_diff_amplitude_2_1", freq="H"),
]

In [13]:
N_FORECASTS = 1
LR = 0.01
EPOCHS = 20

In [14]:
model_classes_and_params = [
    (NeuralProphetModel, {
        "scaler": StandardScaler(),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off",
        "weighted_loss": "std*avg"}),
    (NeuralProphetModel, {
        "scaler": StandardScaler(),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off",
        "weighted_loss": "avg"}),
    (NeuralProphetModel, {
        "scaler": StandardScaler(),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off",
        "weighted_loss": "std"}),
    (NeuralProphetModel, {
        "scaler": StandardScaler(),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off"}),
    (NeuralProphetModel, {
        "scaler": StandardScaler(),
        "scaling_level": "per_dataset",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off"}),
    (NeuralProphetModel, {
        "scaler": MinMaxScaler(feature_range=(-1, 1)),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off",
        "weighted_loss": "std*avg"}),
    (NeuralProphetModel, {
        "scaler": MinMaxScaler(feature_range=(-1, 1)),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off",
        "weighted_loss": "avg"}),
    (NeuralProphetModel, {
        "scaler": MinMaxScaler(feature_range=(-1, 1)),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off",
        "weighted_loss": "std"}),
    (NeuralProphetModel, {
        "scaler": MinMaxScaler(feature_range=(-1, 1)),
        "scaling_level": "per_time_series",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off"}),
    (NeuralProphetModel, {
        "scaler": MinMaxScaler(feature_range=(-1, 1)),
        "scaling_level": "per_dataset",
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off"}),
    (NeuralProphetModel, {
        "n_lags": 24,
        "n_forecasts": N_FORECASTS,
        "learning_rate": LR,
        "epochs": EPOCHS,
        "normalize": "off"}),
]

In [15]:
benchmark = SimpleBenchmark(
    model_classes_and_params=model_classes_and_params,
    datasets=dataset_list,
    metrics=["MAE", "RMSE", "MAPE", "MASE"],
    test_percentage=0.25,
)

In [16]:
results_train, results_test = benchmark.run(verbose=True)

INFO - (tot.benchmark.run) - Experiment list:
INFO - (tot.benchmark.run) - exp 1/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 2/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 3/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 4/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 5/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 6/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 7/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 8/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 9/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 10/11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark.run) - exp 

<PandasArray>
[1169.402732790957, 11073.079455469384, 904.2631836729521]
Length: 3, dtype: float64
<PandasArray>
[155.4760683404663, 2941.890510690241, 192.7708046459482]
Length: 3, dtype: float64


INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - finished exp 1: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - test results 1: {'data': 'similar_season_diff_amplitude_2_1', 'model': 'NeuralProphetModel', 'scaler': StandardScaler(), 'scaling level': 'per_time_series', 'weighted': 'std*avg', 'MAE': 63.213221867879234, 'RMSE': 86.09104407523517, 'MAPE': 1.3274099056919415, 'MASE': 0.3491452452445654}
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - starting exp 2: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
3 missing values in column y were detected in total. 
3 missing values in column y were detected in total.

<PandasArray>
[1169.402732790957, 11073.079455469384, 904.2631836729521]
Length: 3, dtype: float64
<PandasArray>
[155.4760683404663, 2941.890510690241, 192.7708046459482]
Length: 3, dtype: float64


INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - finished exp 2: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - test results 2: {'data': 'similar_season_diff_amplitude_2_1', 'model': 'NeuralProphetModel', 'scaler': StandardScaler(), 'scaling level': 'per_time_series', 'weighted': 'avg', 'MAE': 63.2391029993693, 'RMSE': 86.1184039567072, 'MAPE': 1.3276017581423123, 'MASE': 0.3492881943576512}
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - starting exp 3: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
3 missing values in column y were detected in total. 
3 missing values in column y were detected in total. 
3 mis

...

INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - finished exp 9: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - test results 9: {'data': 'similar_season_diff_amplitude_2_1', 'model': 'NeuralProphetModel', 'scaler': MinMaxScaler(feature_range=(-1, 1)), 'scaling level': 'per_time_series', 'weighted': 'none', 'MAE': 63.32905260721842, 'RMSE': 86.12193538278994, 'MAPE': 1.3294818500677745, 'MASE': 0.34978501253847055}
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - starting exp 10: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
3 missing values in column y were detected in total. 
3 missing values in column y were d

<PandasArray>
[1169.402732790957, 11073.079455469384, 904.2631836729521]
Length: 3, dtype: float64
<PandasArray>
[155.4760683404663, 2941.890510690241, 192.7708046459482]
Length: 3, dtype: float64


INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - finished exp 10: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - test results 10: {'data': 'similar_season_diff_amplitude_2_1', 'model': 'NeuralProphetModel', 'scaler': MinMaxScaler(feature_range=(-1, 1)), 'scaling level': 'per_dataset', 'weighted': 'none', 'MAE': 77.66064071655273, 'RMSE': 104.21091722371665, 'MAPE': 2.1495514859755835, 'MASE': 0.42894259535612833}
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - starting exp 11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
3 missing values in column y were detected in total. 
3 missing values in column y were de

<PandasArray>
[1169.402732790957, 11073.079455469384, 904.2631836729521]
Length: 3, dtype: float64
<PandasArray>
[155.4760683404663, 2941.890510690241, 192.7708046459482]
Length: 3, dtype: float64


INFO - (tot.benchmark._run_exp) - --------------------------------------------------------
INFO - (tot.benchmark._run_exp) - finished exp 11: similar_season_diff_amplitude_2_1_NeuralProphetModel
INFO - (tot.benchmark._run_exp) - test results 11: {'data': 'similar_season_diff_amplitude_2_1', 'model': 'NeuralProphetModel', 'scaler': 'no scaler', 'scaling level': 'per_dataset', 'weighted': 'none', 'MAE': 74.8594102859497, 'RMSE': 102.98829494028831, 'MAPE': 1.5768078776697318, 'MASE': 0.41347057452283487}
INFO - (tot.benchmark._run_exp) - --------------------------------------------------------


In [17]:
results_train

data               model  \
0   similar_season_diff_amplitude_2_1  NeuralProphetModel   
1   similar_season_diff_amplitude_2_1  NeuralProphetModel   
2   similar_season_diff_amplitude_2_1  NeuralProphetModel   
3   similar_season_diff_amplitude_2_1  NeuralProphetModel   
4   similar_season_diff_amplitude_2_1  NeuralProphetModel   
5   similar_season_diff_amplitude_2_1  NeuralProphetModel   
6   similar_season_diff_amplitude_2_1  NeuralProphetModel   
7   similar_season_diff_amplitude_2_1  NeuralProphetModel   
8   similar_season_diff_amplitude_2_1  NeuralProphetModel   
9   similar_season_diff_amplitude_2_1  NeuralProphetModel   
10  similar_season_diff_amplitude_2_1  NeuralProphetModel   

                                 scaler    scaling level weighted        MAE  \
0                      StandardScaler()  per_time_series  std*avg  59.781793   
1                      StandardScaler()  per_time_series      avg  59.796908   
2                      StandardScaler()  per_time_series      std  59.782833   
3                      StandardScaler()  per_time_series     none  60.249058   
4                      StandardScaler()      per_dataset     none  70.382998   
5   MinMaxScaler(feature_range=(-1, 1))  per_time_series  std*avg  59.508506   
6   MinMaxScaler(feature_range=(-1, 1))  per_time_series      avg  59.519359   
7   MinMaxScaler(feature_range=(-1, 1))  per_time_series      std  59.510283   
8   MinMaxScaler(feature_range=(-1, 1))  per_time_series     none  59.907592   
9   MinMaxScaler(feature_range=(-1, 1))      per_dataset     none  74.613898   
10                            no scaler      per_dataset     none  72.138691   

          RMSE      MAPE      MASE  
0    80.270303  1.309023  0.330192  
1    80.286073  1.309109  0.330276  
2    80.270294  1.309047  0.330198  
3    80.713686  1.313192  0.332773  
4    94.802177  1.968560  0.388746  
5    80.007079  1.307961  0.328683  
6    80.017652  1.307988  0.328743  
7    80.007692  1.307992  0.328693  
8    80.355684  1.310962  0.330887  
9    99.012516  2.098647  0.412115  
10  102.269220  1.516196  0.398443

In [18]:
results_test

data               model  \
0   similar_season_diff_amplitude_2_1  NeuralProphetModel   
1   similar_season_diff_amplitude_2_1  NeuralProphetModel   
2   similar_season_diff_amplitude_2_1  NeuralProphetModel   
3   similar_season_diff_amplitude_2_1  NeuralProphetModel   
4   similar_season_diff_amplitude_2_1  NeuralProphetModel   
5   similar_season_diff_amplitude_2_1  NeuralProphetModel   
6   similar_season_diff_amplitude_2_1  NeuralProphetModel   
7   similar_season_diff_amplitude_2_1  NeuralProphetModel   
8   similar_season_diff_amplitude_2_1  NeuralProphetModel   
9   similar_season_diff_amplitude_2_1  NeuralProphetModel   
10  similar_season_diff_amplitude_2_1  NeuralProphetModel   

                                 scaler    scaling level weighted        MAE  \
0                      StandardScaler()  per_time_series  std*avg  63.213222   
1                      StandardScaler()  per_time_series      avg  63.239103   
2                      StandardScaler()  per_time_series      std  63.213793   
3                      StandardScaler()  per_time_series     none  63.925635   
4                      StandardScaler()      per_dataset     none  73.727772   
5   MinMaxScaler(feature_range=(-1, 1))  per_time_series  std*avg  62.723976   
6   MinMaxScaler(feature_range=(-1, 1))  per_time_series      avg  62.743474   
7   MinMaxScaler(feature_range=(-1, 1))  per_time_series      std  62.726040   
8   MinMaxScaler(feature_range=(-1, 1))  per_time_series     none  63.329053   
9   MinMaxScaler(feature_range=(-1, 1))      per_dataset     none  77.660641   
10                            no scaler      per_dataset     none  74.859410   

          RMSE      MAPE      MASE  
0    86.091044  1.327410  0.349145  
1    86.118404  1.327602  0.349288  
2    86.091705  1.327435  0.349148  
3    86.827044  1.334349  0.353080  
4    99.090293  2.065412  0.407220  
5    85.522513  1.324309  0.346443  
6    85.542030  1.324416  0.346551  
7    85.524598  1.324350  0.346454  
8    86.121935  1.329482  0.349785  
9   104.210917  2.149551  0.428943  
10  102.988295  1.576808  0.413471

In [19]:
def plot_forecast(df, regions=regions):
    fig = go.Figure()

    for region in regions:
        fig.add_trace(
            go.Scatter(
                name=region + ' predicted',
                x=df[df['ID'] == region]['ds'],
                y=df[df['ID'] == region]['yhat1']))
        fig.add_trace(
            go.Scatter(
                name=region + ' actual',
                mode="markers",
                x=df[df['ID'] == region]['ds'],
                y=df[df['ID'] == region]['y']))
    fig.show()

In [20]:
plot_forecast(benchmark.fcst_test[0], regions=chosen_regions)

In [21]:
plot_forecast(benchmark.fcst_test[1], regions=chosen_regions)

In [22]:
plot_forecast(benchmark.fcst_test[2], regions=chosen_regions)

In [23]:
plot_forecast(benchmark.fcst_test[3], regions=chosen_regions)

In [24]:
plot_forecast(benchmark.fcst_test[4], regions=chosen_regions)

In [25]:
plot_forecast(benchmark.fcst_test[5], regions=chosen_regions)

In [26]:
plot_forecast(benchmark.fcst_test[6], regions=chosen_regions)

In [27]:
plot_forecast(benchmark.fcst_test[7], regions=chosen_regions)

In [ ]:
plot_forecast(benchmark.fcst_test[8], regions=chosen_regions)